<a name="top"></a>
<div style="width:1000 px">

<div style="float:right; width:98 px; height:98px;">
<img src="https://cdn.miami.edu/_assets-common/images/system/um-logo-gray-bg.png" alt="Miami Logo" style="height: 98px;">
</div>

<h2>Rapid moistening of column water vapor: what's going on there?</h2>
<h3>Drilling down into the science of:</h3>

Mapes, B. E., Chung, E. S., Hannah, W. M., Masunaga, H., Wimmers, A. J., & Velden, C. S. (2018). The meandering margin of the meteorological moist tropics. Geophysical Research Letters, 45. https://doi.org/10.1002/2017GL07644. Free ReadCube viewing at http://rdcu.be/GpqN.

<div style="clear:both"></div>
</div>

<hr style="height:2px;">

### Steps in the analysis 
1. <a href="#import">Importing CWV and AT data</a>
1. <a href="#joint">Joint distributions</a>
1. <a href="#buildclickmap">Build clickable maps in Holoviews</a>
1. <a href="#clickmap">Clickable maps of high AT scenes</a>

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import xarray as xr
from datetime import datetime, timedelta
from IPython.display import HTML,display
from MSEplots import plots as mpt

In [ ]:
%matplotlib inline

<a name="import"></a>
---------
## Open the daily (v4) MIMIC-AT dataset
#### download from here for speed, or use the OpenDAP link in the code cell below
[MIMIC-AT Repository](http://weather.rsmas.miami.edu/repository/entry/show?entryid=0ce7321c-8278-47ef-bb56-7db18c21ea7d), or here [as a single datafile](http://weather.rsmas.miami.edu/repository/entry/show?entryid=synth%3A1142722f-a386-4c17-a4f6-0f685cd19ae3%3AL01JTUlDX2FnZ190ZW1wL01JTUlDLndpdGhfQVQudjQuMjAxNS0yMDE2LjJkZWdfbGF0dHJ1bmMubmM%3D)

In [ ]:
###REMOTE DATASET: 2 years
da = xr.open_dataset('https://weather.rsmas.miami.edu/repository/opendap/synth:0ce7321c-8278-47ef-bb56-7db18c21ea7d:L01JTUlDX0FUX2RhaWx5LjIwMTUtMjAxNl8yZGVnLm5jbWw=/entry.das')

###REMOTE DATASET: 1 month
#da=xr.open_dataset('http://weather.rsmas.miami.edu/repository/opendap/synth:0ce7321c-8278-47ef-bb56-7db18c21ea7d:L01JTUlDLndpdGhfQVQudjQuMjAxNzAzLm5j/entry.das')

###Open local dataset if you downloaded it first
#da=xr.open_dataset('MIMIC.with_AT.v4.2015-2016.2deg_lattrunc.nc')

da

In [ ]:
#Bring in MERRA 3h 3d pressure level dataset
merra2_3d=xr.open_dataset('http://weather.rsmas.miami.edu/repository/opendap/3d1eb24f-d927-4541-a81c-4223d76a0989/entry.das')
merra2_3d=merra2_3d.sel(time=slice(da.time.min(),da.time.max())) #match time bounds
#3h 3d model level dataset
#merra2_3d=xr.open_dataset('http://weather.rsmas.miami.edu/repository/opendap/8e30966a-652a-4dae-bd5c-c587af29de71/entry.das')

<a name="joint"></a>
## General character of the data 
### Joint histogram of TPW and its Lagrangian tendency

In [ ]:
subset = da.sel(time=slice(datetime(2015,1,1),datetime(2015,1,30)))\
           .sel(lat =slice(-30,30))

x = subset.mosaicTPW.data
y = subset.TPW_TEND.data
plt.scatter(x,y); plt.xlim(30,70)

In [ ]:
# To get marginals (see skew and bimodality), use Seaborn
import pandas as pd
import seaborn as sns
# sns.set(color_codes=True)

df = pd.DataFrame({'x': [x], 'y': [y] })
with sns.axes_style("white"): 
    sns.jointplot(x=x, y=y, kind="hex", color="k");

<a name="buildclickmap"></a>

--------------

# Utilities: make clickable map

In [ ]:
import holoviews as hv
from bokeh.models import OpenURL, TapTool, HoverTool
import ipywidgets as widgets
from holoviews.streams import Selection1D
from functools import partial
hv.notebook_extension('bokeh')

In [ ]:
np.warnings.filterwarnings('ignore') # supress lots of error messages from metpy #mostly satvapor pressure cals

### make custom function for drawing coastlines

In [ ]:
def coastlines(resolution='110m',lon_360=False):
    """ A custom method to plot in cylyndrical equi projection, most useful for
        native projections, geoviews currently supports only Web Mercator in
        bokeh mode.
        
        Other resolutions can be 50m
        
        lon_360 flag specifies if longitudes are from -180 to 180 (default) or 0 to 360
        TODO: if hv.Polygons is used instead of overlay it is way faster but 
              something is wrong there.
    """
    try:
        import cartopy.io.shapereader as shapereader
        from cartopy.io.shapereader import natural_earth
        import shapefile
        filename = natural_earth(resolution=resolution,category='physical',name='coastline')
    
        sf = shapefile.Reader(filename)
        fields = [x[0] for x in sf.fields][1:]
        records = sf.records()
        shps = [s.points for s in sf.shapes()]
        pls=[]
        for shp in shps:
            lons=[lo for lo,_ in shp]
            lats=[la for _,la in shp]
            if lon_360:
                lats_patch1=[lat for lon,lat in zip(lons,lats) if lon<0]
                lons_patch1=[lon+360.0 for lon in lons if lon<0]
                if any(lons_patch1):
                    pls.append(hv.Path((lons_patch1,lats_patch1))(style={'color':'Black'}))    
                lats_patch2=[lat if lon>=0 else None for lon,lat in zip(lons,lats)]
                lons_patch2=[lon if lon>=0 else None for lon in lons]
                if any(lons_patch2):
                    pls.append(hv.Path((lons_patch2,lats_patch2))(style={'color':'Black'}))
            else:
                pls.append(hv.Path((lons,lats))(style={'color':'Black'}))
        return hv.Overlay(pls)
    except Exception as err:
        print('Overlaying Coastlines not available from holoviews because: {0}'.format(err))

In [ ]:
coastline=coastlines(lon_360=True) #this may download shape files on first invocation
                                   #if data longitudes are -180 to 180 then lon_360=False

### Create some tools to attach to the plots: hover tool for values

In [ ]:
hover = HoverTool(
        tooltips=[
            ("Time", "@eventtimestr"),
            ("(Lat,Lon)", "(Lon=@eventlonstr{0[.]00}, Lat=@eventlatstr{0[.]00})"),
            ("TPW_TEND","@TPW_TEND"),
            ("TPW","@mosaicTPW")
        ]
    )
#gives info on hovering on a location in the plot

### Create some tools to attach to the plots: tap tool calls the NASA URL! 

In [ ]:
tptool=TapTool()
base_url = 'https://worldview.earthdata.nasa.gov/?p=geographic&l=VIIRS_SNPP_CorrectedReflectance_TrueColor,MODIS_Aqua_CorrectedReflectance_TrueColor(hidden),MODIS_Terra_CorrectedReflectance_TrueColor(hidden),Graticule,AMSR2_Columnar_Water_Vapor_Night(opacity=0.48,palette=rainbow_2,min=45.857742,46.192467,max=49.874477,50.209206,squash),AMSR2_Columnar_Water_Vapor_Day(hidden,opacity=0.3,palette=rainbow_2,min=45.857742,46.192467,max=49.874477,50.209206,squash),Coastlines'
suffix = '&t=@eventdatestr&z=3&v=@eventlonstrW,@eventlatstrS,@eventlonstrE,@eventlatstrN&ab=off&as=@eventdatestr&ae=@eventdatestr1&av=3&al=true'
tptool.callback=OpenURL(url = base_url+suffix)
#on clicking at a point will take to the url specified

### Create some tools to attach to the plots: MSE probe as a widget to attach to the plots:

In [ ]:
def mse_plot(timelatlon,entrain):
    """A function that will produce matplotlib plot at
       a given time,lat,lon
      
    """
    time0,time1,lat,lon=timelatlon.split(' ')
    time=' '.join([time0,time1])
    lat=float(lat)
    lon=float(lon)

    if isinstance(time,str):
        time_str=time
    else:
        np.datetime_as_string(time,units='s')
    
    label='Lat {} Lon {} Time {}'.format(format(lat,'.1f'),format(lon,'.1f'),time_str)
    
    merra2_sel = merra2_3d.sel(time=time,method='nearest').sel(lon=lon,lat=lat,method='nearest')
    
    loadingW.value = "Loading.... "
    
    #filter out nans other wise the plotting/calc routines wont work
    T=merra2_sel.t
    p=merra2_sel.lev[~np.isnan(T)].values #hPa
    qv=merra2_sel.qv[~np.isnan(T)].values  #kg/kg
    
    T=T[~np.isnan(T)].values-273.16 #to deg centigrade ploting function was written in degC
    

    
    plts=mpt.msed_plots(p,T,qv,entrain,title=label)

    loadingW.value='' #label #txt

In [ ]:
# widgets through which interaction happens
times=[' '.join(np.datetime_as_string(tv,unit='s').split('T')) for tv in merra2_3d.time.values] #not necessary but gives nicer formatting

entrainW=widgets.Checkbox(value=False,description='Entraining Parcels')
loadingW=widgets.Label('Loading....') # A informative label to show data is still loading
timelatlonW=widgets.Label(str(times[0]+' 0.0 0.0'))

ui = widgets.VBox([timelatlonW,loadingW,entrainW])

out = widgets.interactive_output(mse_plot, {'timelatlon': timelatlonW,'entrain':entrainW})
out.layout.height='650px' 
out.layout.left='10em' #left padding
#display(ui, out) #shows the widget

In [ ]:
#A callback that updates mse plot on click
def mseplot_callback(data,index):
    
    if isinstance(index,list):
        time=str(data.data.iloc[index[0]]['time'])
        lat=data.data.iloc[index[0]]['lat']
        lon=data.data.iloc[index[0]]['lon']
        timelatlonW.value=f'{time} {lat} {lon}'

### Create list of events and add additional metadata to the dataset: 
#### This step takes a while 

In [ ]:
at_df=da.to_dataframe().reset_index().dropna() #make it pandas dataframe and dropmissing values
at_df['eventdatestr']=at_df.time.apply(lambda x:str(x).split()[0])
at_df['eventdatestr1']=at_df.time.apply(lambda x:str(x+timedelta(days=1)).split()[0])
at_df['eventlonstrE']=at_df.lon.apply(lambda x:str(x+10.0))
at_df['eventlonstrW']=at_df.lon.apply(lambda x:str(x-10.0))
at_df['eventlatstrN']=at_df.lat.apply(lambda x:str(x+7.5))
at_df['eventlatstrS']=at_df.lat.apply(lambda x:str(x-7.5))
at_df['eventtimestr']=at_df.time.apply(str)
at_df['eventlonstr']=at_df.lon.apply(str)
at_df['eventlatstr']=at_df.lat.apply(str)

In [ ]:
def threshold_TPW(threshold=50,max_points=100):
    """ Given a threshold of TPW this function return plot corresponding to locations of first 
        max_points values of TPW_TEND in an increasingly sorted array"""
    
    events=at_df[at_df['mosaicTPW']>threshold].sort_values('TPW_TEND',ascending=False)[0:max_points]
    
    hvd=hv.Dataset(events,kdims=['lon','lat'])
    
    vdims=['TPW_TEND','mosaicTPW','eventtimestr','eventlatstr','eventlonstr',
       'eventdatestr','eventdatestr1','eventlonstrW','eventlonstrE','eventlatstrN','eventlatstrS']
    pts=hvd.to(hv.Points,kdims=['lon','lat'],vdims=vdims).opts(plot={'tools':[hover,tptool]})
    
    #this adds a call back to MSE plot on click
    sel=Selection1D(source=pts)
    callfn=partial(mseplot_callback,data=pts)
    sel.add_subscriber(callfn)
    
    return pts*coastline

<a name="clickmap"></a>

--------------

# Clickable map to see high-AT cloud scenes from Worldview

In [ ]:
%%opts Points  (cmap='viridis' size=0.5) [width=800 height=400 color_index='TPW_TEND' size_index='mosaicTPW' colorbar=True]
threshold_TPW(threshold=40,max_points=1000) #change threshold and maximum number of points 

The color is based on magnitude of TPW_TEND and size of points are based on TPW. 

Notice the box zoom, scroll zoom options: you can zoom in!

on clicking on a data point the plot below responds 

In [ ]:
display(ui,out) #available only in interactive mode

In [ ]:
### Clickable Map with more controls: for embedding into webpages

In [ ]:
%%opts Overlay [width=800 height=500 tools=[hover,tptool] toolbar='above'] {+framewise}
%%opts Points  (cmap='viridis' size=0.6) [color_index='TPW_TEND' size_index='mosaicTPW' colorbar=True colorbar_position='bottom']
#if you have lot of computer resources can make a static map that can also be broswed in a HTML view
#or nbviewer, otherwise see dynamic map below
thresholds = range(40, 70, 10)
max_numbers = range(100,2000, 500)

points_map = {(t, n): threshold_TPW(t,n) for t in thresholds for n in max_numbers}

kdims = [('threshold', 'TPW threshold'), ('max_number', 'Max number')]
holomap = hv.HoloMap(points_map, kdims=kdims)
holomap

In [ ]:
display(ui,out)

In [ ]:
# Below does a dynamic map; where most useful calculations are done on the fly and results are not stored in your browser
#%%opts Overlay [width=800 height=500 tools=[hover,tptool] toolbar='above'] {+framewise}
#%%opts Points  (cmap='viridis' size=0.6) [color_index='TPW_TEND' size_index='mosaicTPW' colorbar=True colorbar_position='bottom']
#hv.DynamicMap(threshold_TPW, kdims=['threshold', 'max_points']).redim.range(threshold=(40,70),max_points=(1000,4000))